In [96]:
import plotly.express as px
import pandas as pd

In [81]:
generation_df = pd.read_csv('data/electricity_generation.csv')
consume_df = pd.read_csv('data/energy_consumption.csv')

In [82]:
generation_df.head()

MSN  YYYYMM       Value  Column_Order   
0  CLETPUS  194913   135451.32             1  \
1  CLETPUS  195013  154519.994             1   
2  CLETPUS  195113  185203.657             1   
3  CLETPUS  195213  195436.666             1   
4  CLETPUS  195313  218846.325             1   

                                         Description                   Unit  
0  Electricity Net Generation From Coal, All Sectors  Million Kilowatthours  
1  Electricity Net Generation From Coal, All Sectors  Million Kilowatthours  
2  Electricity Net Generation From Coal, All Sectors  Million Kilowatthours  
3  Electricity Net Generation From Coal, All Sectors  Million Kilowatthours  
4  Electricity Net Generation From Coal, All Sectors  Million Kilowatthours

In [83]:
consume_df.head()

MSN  YYYYMM     Value  Column_Order   
0  TXRCBUS  194913  4460.588             1  \
1  TXRCBUS  195013  4829.528             1   
2  TXRCBUS  195113  5104.680             1   
3  TXRCBUS  195213  5158.406             1   
4  TXRCBUS  195313  5052.749             1   

                                         Description          Unit  
0  Primary Energy Consumed by the Residential Sector  Trillion Btu  
1  Primary Energy Consumed by the Residential Sector  Trillion Btu  
2  Primary Energy Consumed by the Residential Sector  Trillion Btu  
3  Primary Energy Consumed by the Residential Sector  Trillion Btu  
4  Primary Energy Consumed by the Residential Sector  Trillion Btu

In [84]:
generation_df = generation_df[generation_df['Value'] != generation_df.Value.value_counts().index[0] ]

In [85]:
def dataset_handling(df):
    df = df.drop(['MSN','Column_Order'], axis=1)
    df['Value'] = df.Value.astype('float64')
    df['YYYYMM'] = df.YYYYMM.astype('str')
    df['Month'] = df.YYYYMM.str[4:6]
    df['Year'] = df.YYYYMM.str[0:4]
    df['Type_Month'] = df['Month'].apply(lambda x: 'Normal_Months' if int(x) <13 else 'Month_13' )
    df['Year'] = df.Year.astype(int)
    df['Month'] = df.Month.astype(int)
    df = df[df['Month'] != 13]
    df = df.drop('Type_Month', axis=1)
    df['Date'] = df.YYYYMM.apply(lambda x: str(x[0:4]) + str('-') + str(x[4:]))
    df['Date'] = pd.to_datetime(df.Date, format= '%Y-%m')    
    
    return df 

    

In [86]:
generation = dataset_handling(generation_df)
consume = dataset_handling(consume_df)

In [87]:
consume.head()

YYYYMM     Value                                        Description   
24  197301  1339.270  Primary Energy Consumed by the Residential Sector  \
25  197302  1174.899  Primary Energy Consumed by the Residential Sector   
26  197303   983.374  Primary Energy Consumed by the Residential Sector   
27  197304   715.391  Primary Energy Consumed by the Residential Sector   
28  197305   535.914  Primary Energy Consumed by the Residential Sector   

            Unit  Month  Year       Date  
24  Trillion Btu      1  1973 1973-01-01  
25  Trillion Btu      2  1973 1973-02-01  
26  Trillion Btu      3  1973 1973-03-01  
27  Trillion Btu      4  1973 1973-04-01  
28  Trillion Btu      5  1973 1973-05-01

In [88]:
generation.head()

YYYYMM      Value                                        Description   
24  197301  75190.149  Electricity Net Generation From Coal, All Sectors  \
25  197302  67797.946  Electricity Net Generation From Coal, All Sectors   
26  197303  67387.612  Electricity Net Generation From Coal, All Sectors   
27  197304  63935.049  Electricity Net Generation From Coal, All Sectors   
28  197305  64927.181  Electricity Net Generation From Coal, All Sectors   

                     Unit  Month  Year       Date  
24  Million Kilowatthours      1  1973 1973-01-01  
25  Million Kilowatthours      2  1973 1973-02-01  
26  Million Kilowatthours      3  1973 1973-03-01  
27  Million Kilowatthours      4  1973 1973-04-01  
28  Million Kilowatthours      5  1973 1973-05-01

In [89]:
generation['Description'] = generation['Description'].replace(
    to_replace=[r"Electricity Net Generation From", r", All Sectors"], value=['ENRG', ''], regex=True)
generation.Description.unique()

consume['Description'] = consume.Description.replace(
    to_replace=['Total Energy Consumed', 'Primary Energy Consumed', 'by the ', ' Sector', 'Primary Energy Consumption'],
    value=['TEC', 'PEC', '', '', 'PE Consumption'], regex=True
)
consume.Description.unique()

array(['PEC Residential', 'TEC Residential', 'PEC Commercial',
       'TEC Commercial', 'PEC Industrial', 'TEC Industrial',
       'PEC Transportation', 'TEC Transportation', 'PEC Electric Power',
       'Energy Consumption Balancing Item', 'PE Consumption Total'],
      dtype=object)

In [90]:
consume_df.Description.unique()

array(['Primary Energy Consumed by the Residential Sector',
       'Total Energy Consumed by the Residential Sector',
       'Primary Energy Consumed by the Commercial Sector',
       'Total Energy Consumed by the Commercial Sector',
       'Primary Energy Consumed by the Industrial Sector',
       'Total Energy Consumed by the Industrial Sector',
       'Primary Energy Consumed by the Transportation Sector',
       'Total Energy Consumed by the Transportation Sector',
       'Primary Energy Consumed by the Electric Power Sector',
       'Energy Consumption Balancing Item',
       'Primary Energy Consumption Total'], dtype=object)

In [91]:
generation.head()

YYYYMM      Value Description                   Unit  Month  Year   
24  197301  75190.149   ENRG Coal  Million Kilowatthours      1  1973  \
25  197302  67797.946   ENRG Coal  Million Kilowatthours      2  1973   
26  197303  67387.612   ENRG Coal  Million Kilowatthours      3  1973   
27  197304  63935.049   ENRG Coal  Million Kilowatthours      4  1973   
28  197305  64927.181   ENRG Coal  Million Kilowatthours      5  1973   

         Date  
24 1973-01-01  
25 1973-02-01  
26 1973-03-01  
27 1973-04-01  
28 1973-05-01

In [92]:
def gen_merged_sector(sector_consumed, sector_produced):
    con_df = consume[consume['Description'] == sector_consumed].copy()
    gen_df = generation[generation['Description'] == sector_produced].copy()

    con_df = con_df.drop(['Description', 'Unit', 'Month', 'Year', 'Date'], axis=1)
    gen_df = gen_df.drop(['Description', 'Unit'], axis=1)

    merged = con_df.merge(gen_df, on= 'YYYYMM')
    merged = merged.rename(columns= {'Value_x':'Consumed', 'Value_y':'Generated'})
    
    return merged


electric_nuclear = gen_merged_sector('PEC Electric Power', 'ENRG Nuclear Electric Power')
electric_nuclear

YYYYMM  Consumed  Generated  Month  Year       Date
0    197301  1691.096   6246.251      1  1973 1973-01-01
1    197302  1511.458   5928.069      2  1973 1973-02-01
2    197303  1559.159   6649.007      3  1973 1973-03-01
3    197304  1470.152   5876.392      4  1973 1973-04-01
4    197305  1551.631   5696.657      5  1973 1973-05-01
..      ...       ...        ...    ...   ...        ...
557  201906  3180.175  68804.879      6  2019 2019-06-01
558  201907  3701.225  72198.595      7  2019 2019-07-01
559  201908  3601.167  71910.684      8  2019 2019-08-01
560  201909  3230.691  65892.180      9  2019 2019-09-01
561  201910  2877.253  62032.622     10  2019 2019-10-01

[562 rows x 6 columns]

In [95]:
m_consume = consume.drop(['Description', 'Unit', 'Month', 'Year', 'Date'], axis=1)
m_generation = generation.drop(['Description', 'Unit'], axis=1)
gen_cons_energy = m_consume.merge(m_generation, on="YYYYMM")
gen_cons_energy = gen_cons_energy.rename(columns={'Value_x':'Consumed', 'Value_y':'Generated'})
gen_cons_energy


YYYYMM  Consumed   Generated  Month  Year       Date
0      197301  1339.270   75190.149      1  1973 1973-01-01
1      197301  1339.270   31183.619      1  1973 1973-01-01
2      197301  1339.270   21184.967      1  1973 1973-01-01
3      197301  1339.270    6246.251      1  1973 1973-01-01
4      197301  1339.270   26249.203      1  1973 1973-01-01
...       ...       ...         ...    ...   ...        ...
73233  201910  7976.769    1565.985     10  2019 2019-10-01
73234  201910  7976.769    1276.179     10  2019 2019-10-01
73235  201910  7976.769    6109.899     10  2019 2019-10-01
73236  201910  7976.769   28143.676     10  2019 2019-10-01
73237  201910  7976.769  321921.812     10  2019 2019-10-01

[73238 rows x 6 columns]

In [102]:
gen_cons_energy.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 73238 entries, 0 to 73237
Data columns (total 6 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   YYYYMM     73238 non-null  object        
 1   Consumed   73238 non-null  float64       
 2   Generated  73238 non-null  float64       
 3   Month      73238 non-null  int32         
 4   Year       73238 non-null  int32         
 5   Date       73238 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(2), int32(2), object(1)
memory usage: 2.8+ MB


In [98]:
px.line(data_frame=gen_cons_energy, x='Date',y='Consumed')


ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'hovertemplate': 'Date=%{x}<br>Consumed=%{y}<extra></extra>',
              'legendgroup': '',
              'line': {'color': '#636efa', 'dash': 'solid'},
              'marker': {'symbol': 'circle'},
              'mode': 'lines',
              'name': '',
              'showlegend': False,
              'type': 'scattergl',
              'x': array([datetime.datetime(1973, 1, 1, 0, 0),
                          datetime.datetime(1973, 1, 1, 0, 0),
                          datetime.datetime(1973, 1, 1, 0, 0), ...,
                          datetime.datetime(2019, 10, 1, 0, 0),
                          datetime.datetime(2019, 10, 1, 0, 0),
                          datetime.datetime(2019, 10, 1, 0, 0)], dtype=object),
              'xaxis': 'x',
              'y': array([1339.27 , 1339.27 , 1339.27 , ..., 7976.769, 7976.769, 7976.769]),
              'yaxis': 'y'}],
    'layout': {'legend': {'tracegroupgap': 0},
               'margin': {'t': 60},
               'template': '...',
               'xaxis': {'anchor': 'y', 'domain': [0.0, 1.0], 'title': {'text': 'Date'}},
               'yaxis': {'anchor': 'x', 'domain': [0.0, 1.0], 'title': {'text': 'Consumed'}}}
})

"nbformat" no se reconoce como un comando interno o externo,
programa o archivo por lotes ejecutable.
